# Cours 3 : Machine Learning - Algorithmes supervisés (1/2)

## Préambule

Les objectifs de cette séance (3h) sont :
* Préparation des bases de modélisation (sampling)
* Mettre en application un modèle supervisé simple.
* Construire un modèle de Machine Learning (cross-validation et hyperparamétrage) pour résoudre un problème de régression
* Analyser les performances du modèle

## Préparation du workspace

### Import de librairies 

In [56]:
# Données
import numpy as np
import pandas as pd

#Graphiques
import seaborn as sns

sns.set()
import plotly.express as px
import plotly.graph_objects as gp
import sklearn.metrics as metrics
import sklearn.preprocessing as preproc

#Statistiques
from scipy.stats import chi2_contingency

# Machine Learning
from sklearn.cluster import KMeans
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import KFold, train_test_split
from sklearn.tree import DecisionTreeClassifier, DecisionTreeRegressor


### Définition des fonctions 

### Constantes

In [57]:
input_path = "./1_inputs"
output_path = "./2_outputs"

### Import des données

In [58]:
path =input_path + '/base_retraitee.csv'
data_retraitee = pd.read_csv(path,sep=",",decimal=".")

## Algorithme supervisé : CART 

Dans cette partie l'objectif est de construire un modèle simple (algorithme CART) afin de voir les différentes étapes nécessaire au lancement d'un modèle
Nous modéliserons directement le coût des sinistres. 

### Construction du modèle

La première étape est de calculer les côut moyen de chaque sinistre (target ou variable réponse). Cette variable sera la variable à prédire en fonction des variables explicatives.

In [59]:
data_model = data_retraitee.copy()

# Filtre pour ne garder que les lignes qui ont un sinistre (NB > 0)
data_model = data_model[data_model['NB'] > 0]

# Calcul du cout moyen "théorique" des sinistres
data_model["CM"] = (data_model["CHARGE"] / data_model["NB"])
data_model = data_model.drop(['CHARGE', 'NB', "EXPO"], axis=1)
data_model.shape

(824, 14)

**Exercice :** construisez les statistiques descriptives de la base utilisée.

In [60]:
data_model.describe(include='all')

ANNEE_CTR CONTRAT_ANCIENNETE FREQUENCE_PAIEMENT_COTISATION  \
count    824.000000                824                           824   
unique          NaN                  5                             3   
top             NaN              (0,1]                       MENSUEL   
freq            NaN                297                           398   
mean    2018.384709                NaN                           NaN   
std        1.515833                NaN                           NaN   
min     2016.000000                NaN                           NaN   
25%     2017.000000                NaN                           NaN   
50%     2018.000000                NaN                           NaN   
75%     2020.000000                NaN                           NaN   
max     2021.000000                NaN                           NaN   

        GROUPE_KM ZONE_RISQUE  AGE_ASSURE_PRINCIPAL GENRE DEUXIEME_CONDUCTEUR  \
count         824         824            824.000000   824                 824   
unique          4          14                   NaN     2                   2   
top     [0;20000[           C                   NaN     M               False   
freq          391         269                   NaN   483                 663   
mean          NaN         NaN             44.383495   NaN                 NaN   
std           NaN         NaN             13.808217   NaN                 NaN   
min           NaN         NaN             19.000000   NaN                 NaN   
25%           NaN         NaN             34.000000   NaN                 NaN   
50%           NaN         NaN             43.000000   NaN                 NaN   
75%           NaN         NaN             53.000000   NaN                 NaN   
max           NaN         NaN             94.000000   NaN                 NaN   

        ANCIENNETE_PERMIS  ANNEE_CONSTRUCTION  ENERGIE EQUIPEMENT_SECURITE  \
count          824.000000          824.000000      824                 824   
unique                NaN                 NaN        3                   2   
top                   NaN                 NaN  ESSENCE                FAUX   
freq                  NaN                 NaN      413                 517   
mean            35.688107         2015.212379      NaN                 NaN   
std             19.370621            3.163782      NaN                 NaN   
min              1.000000         1998.000000      NaN                 NaN   
25%             18.000000         2014.000000      NaN                 NaN   
50%             35.000000         2016.000000      NaN                 NaN   
75%             53.000000         2017.000000      NaN                 NaN   
max             70.000000         2021.000000      NaN                 NaN   

       VALEUR_DU_BIEN            CM  
count             824    824.000000  
unique              6           NaN  
top     [10000;15000[           NaN  
freq              213           NaN  
mean              NaN   4246.016978  
std               NaN   6869.616917  
min               NaN      7.500000  
25%               NaN   1159.961250  
50%               NaN   2541.650000  
75%               NaN   4193.797500  
max               NaN  83421.850000

#### Etude des corrélations parmi les variables explicatives

**Question :** Selon vous, pourquoi faut-il s'intéresser à la corrélation des variables ? 

*Réponse*: Pour avoir un modèle qui fit mieux + déterminer un potentiel effet de causalité entre features et target + sélectionner certaines variables.

In [61]:
data_set = data_model.drop("CM", axis=1)
data_set.shape

(824, 13)

In [62]:
#Séparation en variables qualitatives ou catégorielles
variables_na = []
variables_numeriques = []
variables_01 = []
variables_categorielles = []
for colu in data_set.columns:
    if True in data_set[colu].isna().unique() :
        variables_na.append(data_set[colu])
    else :
        if str(data_set[colu].dtypes) in ["int32","int64","float64"]:
            if len(data_set[colu].unique())==2 :
                variables_categorielles.append(data_set[colu])
            else :
                variables_numeriques.append(data_set[colu])
        else :
            if len(data_set[colu].unique())==2 :
                variables_categorielles.append(data_set[colu])
            else :
                variables_categorielles.append(data_set[colu])

##### Corrélation des variables catégorielles :

In [63]:
vars_categorielles = pd.DataFrame(variables_categorielles).transpose()

In [64]:
# Matrice de corrélation pour les variables catégorielles (V de Cramér)
def cramers_v(confusion_matrix):
    """Calcule le V de Cramér à partir d'une matrice de contingence"""
    chi2 = chi2_contingency(confusion_matrix)[0]
    n = confusion_matrix.sum().sum()
    phi2 = chi2 / n
    r, k = confusion_matrix.shape
    phi2corr = max(0, phi2 - ((k-1)*(r-1))/(n-1))
    rcorr = r - ((r-1)**2)/(n-1)
    kcorr = k - ((k-1)**2)/(n-1)
    return np.sqrt(phi2corr / min((kcorr-1), (rcorr-1)))

# Créer la matrice de corrélation
categorical_cols = vars_categorielles.columns
n_vars = len(categorical_cols)
cramers_matrix = np.zeros((n_vars, n_vars))

for i, col1 in enumerate(categorical_cols):
    for j, col2 in enumerate(categorical_cols):
        if i == j:
            cramers_matrix[i, j] = 1.0
        else:
            confusion_matrix = pd.crosstab(vars_categorielles[col1], vars_categorielles[col2])
            cramers_matrix[i, j] = cramers_v(confusion_matrix)

# Créer le DataFrame de corrélation
correlation_cat = pd.DataFrame(cramers_matrix,
                               index=categorical_cols,
                               columns=categorical_cols)

# Visualiser avec Plotly
fig = px.imshow(correlation_cat,
                text_auto='.2f', # type: ignore
                aspect="auto",
                color_continuous_scale='RdBu_r',
                title='Matrice de corrélation des variables catégorielles (V de Cramér)')
fig.show()

##### Corrélation des variables numériques :

In [65]:
vars_numeriques = pd.DataFrame(variables_numeriques).transpose()

In [66]:
vars_numeriques.corr()
fig = px.imshow(vars_numeriques.corr(),
                text_auto=True,
                aspect="auto",
                color_continuous_scale='RdBu_r',
                title='Matrice de corrélation des variables numériques')
fig.show()

**Question :** quels sont vos commentaires ?

*Réponse*: Aucune des variables ne semblent corrélées.

#### Preprocessing

Deux étapes sont nécessaires avant de lancer l'apprentissage d'un modèle, c'est ce qu'on connait comme le *Preprocessing* :

* Les modèles proposés par la librairie "sklearn" ne gèrent que des variables numériques. Il est donc nécessaire de transformer les variables catégorielles en variables numériques : ce processus s'appelle le *One Hot Encoding*.
* Normaliser les données numériques

**Exercice :** proposez un bout de code permettant de réaliser le One Hot Encoding des variables catégorielles. Vous pourrez utiliser la fonction "preproc.OneHotEncoder" de la librairie sklearn

In [67]:
encoder = preproc.OneHotEncoder()
encoder.fit(vars_categorielles)
vars_categorielles_enc = encoder.transform(vars_categorielles)
vars_categorielles_enc = pd.DataFrame(vars_categorielles_enc.toarray(), columns=encoder.get_feature_names_out(vars_categorielles.columns))

**Exercice :** proposez un bout de code permettant normaliser les variables numériques présentes dans la base. Vous pourrez utiliser la fonction "preproc.StandardScaler" de la librairie sklearn

In [68]:
scaler = preproc.StandardScaler()
scaler.fit(vars_numeriques)
vars_numeriques_scaled = scaler.transform(vars_numeriques)
vars_numeriques_scaled = pd.DataFrame(vars_numeriques_scaled, columns=vars_numeriques.columns)

#### Sampling

**Exercice :** proposez un bout de code permettant construire la base d'apprentissage (80% des données) et la base de test (20%).

In [69]:
X = data_model_preprocessed = vars_numeriques_scaled.merge(vars_categorielles_enc, left_index=True, right_index=True) # type: ignore
Y = data_model["CM"]

X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.2, random_state=42
)

#### Fitting

**Exercice :** proposez un bout de code permettant construire le modèle

In [70]:
tree = DecisionTreeRegressor()
tree.fit(X_train, y_train)

DecisionTreeRegressor()

**Exercice :** proposez un bout de code permettant d'évaluer les performances du modèle (MAE, MSE et RMSE)

In [71]:
# Prédictions sur l'ensemble d'entraînement
y_pred_train = tree.predict(X_train)

mae = metrics.mean_absolute_error(y_train, y_pred_train)
mse = metrics.mean_squared_error(y_train, y_pred_train)
rmse = metrics.root_mean_squared_error(y_train, y_pred_train)

print(f"MAE: {mae:.2f}")
print(f"MSE: {mse:.2f}")
print(f"RMSE: {rmse:.2f}")

MAE: 0.00
MSE: 0.00
RMSE: 0.00


In [72]:
y_pred_test = tree.predict(X_test)

mae = metrics.mean_absolute_error(y_test, y_pred_test)
mse = metrics.mean_squared_error(y_test, y_pred_test)
rmse = metrics.root_mean_squared_error(y_test, y_pred_test)

print(f"MAE: {mae:.2f}")
print(f"MSE: {mse:.2f}")
print(f"RMSE: {rmse:.2f}")


MAE: 5124.14
MSE: 84535204.52
RMSE: 9194.30


**Question :** que pensez-vous des performances de ce modèle ?

*Réponse*: 

Erreur Absolue Moyenne (MAE)
La MAE représente l'écart absolu moyen entre les prédictions du modèle et les valeurs réelles. Une MAE de 5950.05 signifie qu'en moyenne, notre modèle commet une erreur de cette magnitude, dans l'unité de la variable cible. C'est l'indicateur le plus direct de l'erreur de prédiction moyenne.

Racine de l'Erreur Quadratique Moyenne (RMSE)
La RMSE est la racine carrée de la moyenne des erreurs au carré ($RMSE = \sqrt{MSE}$). En raison de l'opération de mise au carré, cette métrique est particulièrement sensible aux grandes erreurs. La valeur obtenue est de 12651.79.

## Algorithme supervisé : Random Forest  

A ce stade, nous avons vu les différentes étapes pour lancer un algorithme de Machine Learning. Néanmoins, ces étapes ne sont pas suffisantes pour construire un modèle performant.  
En effet, afin de construire un modèle performant le Data Scientist doit agir sur l'apprentissage du modèle. Dans ce qui suit nous :
* Changerons d'algorithme pour utiliser un algorithme plus performant (Random Forest)
* Raliserons un *grid search* sur les paramètres du modèle
* Appliquerons l'apprentissage par validation croisée


### Modèle avec Validation Croisée

#### Sampling

In [73]:
X = data_model_preprocessed
Y = data_model["CM"]

X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.2, random_state=42
)

#### Fitting avec Cross-Validation

**Exercice :** construisez un modèle RF (RandomForestRegressor) en implémentant la technique de validation croisée. Pensez à enregistrer au sein d'une variable/liste les performances (MAE, MSE & RMSE) du modèle au sein de chaque fold.

In [74]:
# Initialisation
# Nombre de sous-échantillons pour la cross-validation
num_splits = 5

# Random Forest regressor
rf_regressor = RandomForestRegressor(n_estimators=100, random_state=42)

# Initialisation du KFold cross-validation splitter
kf = KFold(n_splits=num_splits)

# Listes pour enregistrer les performances du modèle
MAE_scores = []
MSE_scores = []
RMSE_scores = []

In [75]:
# Entrainement avec cross-validation
for train_index, val_index in kf.split(X_train):
    X_train_fold, X_val_fold = X_train.iloc[train_index], X_train.iloc[val_index]
    y_train_fold, y_val_fold = y_train.iloc[train_index], y_train.iloc[val_index]

    rf_regressor.fit(X_train_fold, y_train_fold)
    y_pred_fold = rf_regressor.predict(X_val_fold)

    mae = metrics.mean_absolute_error(y_val_fold, y_pred_fold)
    mse = metrics.mean_squared_error(y_val_fold, y_pred_fold)
    rmse = metrics.root_mean_squared_error(y_val_fold, y_pred_fold)

    MAE_scores.append(mae)
    MSE_scores.append(mse)
    RMSE_scores.append(rmse)

print(f"Validation croisée terminée avec {len(MAE_scores)} folds")

Validation croisée terminée avec 5 folds


In [76]:
# Métriques sur tous les folds

#MAE
for fold, mae in enumerate(MAE_scores, start=1):
    print(f"Fold {fold} MAE:", mae)

Fold 1 MAE: 4472.5486946969695
Fold 2 MAE: 3859.4743234848484
Fold 3 MAE: 3633.0231541666662
Fold 4 MAE: 3888.3910715909087
Fold 5 MAE: 4808.59621832061


In [77]:
#MSE
for fold, mse in enumerate(MSE_scores, start=1):
    print(f"Fold {fold} MSE:", mse)

Fold 1 MSE: 85464414.44080053
Fold 2 MSE: 34396997.21755034
Fold 3 MSE: 55184512.50786593
Fold 4 MSE: 33191300.80751679
Fold 5 MSE: 68739370.63588645


In [78]:
#RMSE
for fold, rmse in enumerate(RMSE_scores, start=1):
    print(f"Fold {fold} RMSE:", rmse)

Fold 1 RMSE: 9244.696557529649
Fold 2 RMSE: 5864.895328780415
Fold 3 RMSE: 7428.62790210049
Fold 4 RMSE: 5761.189183451346
Fold 5 RMSE: 8290.9209763383


**Question :** Commentez les résultats.

### Ajout d'un Grid Search pour les hyper paramètres

#### Sampling

In [ ]:
X = data_model_preprocessed
Y = data_model["CM"]

X_train, X_test, y_train, y_test = train_test_split(
    X, Y, test_size=0.2, random_state=42
)

#### Fitting avec Cross-Validation et *Grid Search*

**Exercice :** Intégrez la technique de Grid Search pour rechercher les paramètres optimaux du modèle.

In [ ]:
#Initialisation
# Nombre de sous-échantillons pour la cross-validation
num_splits = 5

# Initialisation du KFold cross-validation splitter
kf = KFold(n_splits=num_splits)

# Listes pour enregistrer les performances du modèle
MAE_scores = []
MSE_scores = []
RMSE_scores = []

# Hyperparamètres à tester
n_estimators_values = []
max_depth_values = []
min_samples_split_values = []

# Liste pour sauveagrder les meilleurs résultats
best_score = np.inf
best_params = {}

MAE_best_score = []
MSE_best_score = []
RMSE_best_score = []

In [87]:
#Complétez ici avec votre code
for n_estimators in n_estimators_values:
    for max_depth in max_depth_values:
        for min_samples_split in min_samples_split_values:
            rf_regressor = RandomForestRegressor(
                n_estimators=n_estimators,
                max_depth=max_depth,
                min_samples_split=min_samples_split,
                random_state=42
            )
            MAE_scores = []
            MSE_scores = []
            RMSE_scores = []

            for train_index, val_index in kf.split(X_train):
                X_train_fold, X_val_fold = X_train.iloc[train_index], X_train.iloc[val_index]
                y_train_fold, y_val_fold = y_train.iloc[train_index], y_train.iloc[val_index]

                rf_regressor.fit(X_train_fold, y_train_fold)
                y_pred_fold = rf_regressor.predict(X_val_fold)

                mae = metrics.mean_absolute_error(y_val_fold, y_pred_fold)
                mse = metrics.mean_squared_error(y_val_fold, y_pred_fold)
                rmse = metrics.root_mean_squared_error(y_val_fold, y_pred_fold)

                MAE_scores.append(mae)
                MSE_scores.append(mse)
                RMSE_scores.append(rmse)

            avg_mae = np.mean(MAE_scores)
            avg_mse = np.mean(MSE_scores)
            avg_rmse = np.mean(RMSE_scores)

            if avg_rmse < best_score:
                best_score = avg_rmse
                best_params = {
                    'n_estimators': n_estimators,
                    'max_depth': max_depth,
                    'min_samples_split': min_samples_split
                }
                MAE_best_score = MAE_scores
                MSE_best_score = MSE_scores
                RMSE_best_score = RMSE_scores

In [88]:
# Meilleurs résultats
print("Meilleurs paramètres:", best_params)
print("Meilleure RMSE :", best_score)

Meilleurs paramètres: {}
Meilleure RMSE : inf


In [82]:
# Métriques sur tous les folds

#RMSE
for fold, rmse in enumerate(RMSE_best_score, start=1):
    print(f"Fold {fold} RMSE:", rmse)


In [83]:
#MAE
for fold, mse in enumerate(MSE_best_score, start=1):
    print(f"Fold {fold} MSE:", mse)

In [84]:
#MSE
for fold, mae in enumerate(MAE_best_score, start=1):
    print(f"Fold {fold} MAE:", mae)

**Question :** Commentez les résultats